# Informacja o danych

Dane pochchodzą ze zbiorów Kaggle do których link znajduje się poniżej

https://www.kaggle.com/datasets/pritish509/s-and-p-500-esg-risk-ratings

# Instalacja pakietów i bibliotek

In [2]:
! pip install ydata-profiling

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 357.9/357.9 kB 5.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 102.7/102.7 kB 8.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 686.1/686.1 kB 14.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 293.3/293.3 kB 14.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 15.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.7/4.7 MB 31.3 MB/s eta 0:00:00
  Created wheel for htmlmin: filename=htmlmin-0.1.12-py3-none-any.whl size=27081 sha256=d054ab83198d0579cb5deb2c5326f1ca8fab481426b27865d68cff257a0cf35f
  Stored in directory: /root/.cache/pip/wheels/dd/91/29/a79cecb328d01739e64017b6fb9a1ab9d8cb1853098ec5966d
Successfully built htmlmin
  Attempting uninstall: seaborn
    Found existing installation: seaborn 0.13.1
    Uninstalling seaborn-0.13.1:
      Successfully uninstalled seaborn-0.13.1


In [3]:
import numpy as np
import pandas as pd
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler,LabelEncoder
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from xgboost import XGBClassifier
from sklearn.metrics import accuracy_score, classification_report
from sklearn.model_selection import GridSearchCV
from imblearn.over_sampling import SMOTE
from sklearn.metrics import classification_report
from ydata_profiling import ProfileReport

# Wczytanie danych

In [4]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [5]:
data = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/SP 500 ESG Risk Ratings.csv')

# EDA

In [6]:
data.head()

Symbol                         Name  \
0      A     Agilent Technologies Inc   
1    AAL  American Airlines Group Inc   
2    AAP       Advance Auto Parts Inc   
3   AAPL                    Apple Inc   
4   ABBV                   Abbvie Inc   

                                             Address             Sector  \
0  5301 Stevens Creek Boulevard\nSanta Clara, CA ...         Healthcare   
1  1 Skyview Drive\nFort Worth, TX 76155\nUnited ...        Industrials   
2  4200 Six Forks Road\nRaleigh, NC 27609\nUnited...  Consumer Cyclical   
3  One Apple Park Way\nCupertino, CA 95014\nUnite...         Technology   
4  1 North Waukegan Road\nNorth Chicago, IL 60064...         Healthcare   

                     Industry Full Time Employees  \
0      Diagnostics & Research              18,000   
1                    Airlines             132,500   
2            Specialty Retail              40,000   
3        Consumer Electronics             164,000   
4  Drug Manufacturers—General              50,000   

                                         Description  Total ESG Risk score  \
0  Agilent Technologies, Inc. provides applicatio...                  15.0   
1  American Airlines Group Inc., through its subs...                  29.0   
2  Advance Auto Parts, Inc. provides automotive r...                  12.0   
3  Apple Inc. designs, manufactures, and markets ...                  17.0   
4  AbbVie Inc. discovers, develops, manufactures,...                  28.0   

   Environment Risk Score  Governance Risk Score  Social Risk Score  \
0                     0.3                    6.3                8.6   
1                    12.0                    5.0               12.0   
2                     0.0                    3.0                8.0   
3                     0.6                    9.2                6.9   
4                     1.1                    9.9               16.8   

  Controversy Level  Controversy Score ESG Risk Percentile ESG Risk Level  
0               Low                1.0     11th percentile            Low  
1          Moderate                2.0     62nd percentile            NaN  
2          Moderate                2.0      4th percentile     Negligible  
3       Significant                3.0     15th percentile            Low  
4       Significant                3.0     55th percentile         Medium

In [8]:
profile = ProfileReport(data, title="Profiling Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 503 entries, 0 to 502
Data columns (total 15 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   Symbol                  503 non-null    object 
 1   Name                    503 non-null    object 
 2   Address                 501 non-null    object 
 3   Sector                  501 non-null    object 
 4   Industry                501 non-null    object 
 5   Full Time Employees     496 non-null    object 
 6   Description             501 non-null    object 
 7   Total ESG Risk score    433 non-null    float64
 8   Environment Risk Score  433 non-null    float64
 9   Governance Risk Score   433 non-null    float64
 10  Social Risk Score       433 non-null    float64
 11  Controversy Level       404 non-null    object 
 12  Controversy Score       433 non-null    float64
 13  ESG Risk Percentile     433 non-null    object 
 14  ESG Risk Level          376 non-null    ob

Usunięcie zwartości zerowych

In [10]:
df = data[data['Total ESG Risk score'] > 0]

Usunięcie wartości NaN

In [11]:
df = df.dropna(subset=['ESG Risk Level'])

In [18]:
X = df[['Total ESG Risk score', 'Controversy Score']]
y = df['ESG Risk Level']


Podział zbioru na treningowy i testowy

In [27]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, stratify=y)


Zmiana wartości kategorycznej na numeryczną etykiety ESG Risk Level

In [26]:
label_encoder = LabelEncoder()
y = label_encoder.fit_transform(y)

Ponieważ dane są niezbalansowane zatosowane zostało SMOTE- metoda ta generuje syntetyczne dane dla klasy mniejszościowej

In [32]:
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X, y)

Skalowanie danych

In [33]:
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X_resampled)

Podział zbiorów na treningowy i testowy

In [34]:
X_train, X_test, y_train, y_test = train_test_split(X_scaled, y_resampled, test_size=0.2, stratify=y_resampled, random_state=42)

# Model uczenia maszynowego

Budowanie siatki modeli

In [35]:
models = {
    'Logistic Regression': LogisticRegression(),
    'Decision Tree': DecisionTreeClassifier(),
    'Random Forest': RandomForestClassifier(),
    'SVM': SVC(),
    'KNN': KNeighborsClassifier(),
    'Gradient Boosting': GradientBoostingClassifier(),
    'XGBoost': XGBClassifier()
}

Budowanie siatki paremetrów

In [36]:
param_grids = {
    'Logistic Regression': {'C': [0.001, 0.01, 0.1, 1, 10, 100]},
    'Decision Tree': {'max_depth': [3, 5, 7, None]},
    'Random Forest': {'n_estimators': [50, 100, 200]},
    'SVM': {'C': [0.1, 1, 10], 'gamma': [0.1, 1, 10]},
    'KNN': {'n_neighbors': [3, 5, 7]},
    'Gradient Boosting': {'n_estimators': [50, 100, 200], 'learning_rate': [0.05, 0.1, 0.2]},
    'XGBoost': {'n_estimators': [50, 100, 200], 'learning_rate': [0.05, 0.1, 0.2]}
}

In [24]:
predictions = {}

Dobór najlepszych parametrów i trenowanie modeli

In [37]:
for name, model in models.items():
    if name in param_grids:
        grid_search = GridSearchCV(model, param_grids[name], cv=5)
        grid_search.fit(X_train, y_train)
        model = grid_search.best_estimator_
    model.fit(X_train, y_train)
    predictions[name] = model.predict(X_test)

Wyświetlanie wyników

In [38]:
for name, prediction in predictions.items():
    print(f"Model: {name}")
    print(classification_report(y_test, prediction))

Model: Logistic Regression
              precision    recall  f1-score   support

           0       0.58      0.41      0.48        27
           1       0.47      0.54      0.50        26
           2       0.93      0.93      0.93        27
           3       0.48      0.41      0.44        27
           4       0.54      0.70      0.61        27

    accuracy                           0.60       134
   macro avg       0.60      0.60      0.59       134
weighted avg       0.60      0.60      0.59       134

Model: Decision Tree
              precision    recall  f1-score   support

           0       0.72      0.67      0.69        27
           1       0.56      0.77      0.65        26
           2       0.89      0.93      0.91        27
           3       0.68      0.48      0.57        27
           4       0.77      0.74      0.75        27

    accuracy                           0.72       134
   macro avg       0.72      0.72      0.71       134
weighted avg       0.73      